In [2]:
import os
import re
import pandas as pd
from bs4 import BeautifulSoup
import sqlite3

In [32]:
# Base directory where SEC filings are stored
base_dir = "C:/Users/sudet/Desktop/sec-edgar-filings"  # Update this with the correct path
output_file = "sec_filings.csv"

In [ ]:
"""def extract_metadata(text):
    """"""Extract metadata such as company name, CIK, filing type, and date.""""""
    metadata = {}
    
    company_name_match = re.search(r"COMPANY CONFORMED NAME:\s+(.+)", text)
    cik_match = re.search(r"CENTRAL INDEX KEY:\s+(\d+)", text)
    filing_type_match = re.search(r"FORM TYPE:\s+(\S+)", text)
    filed_date_match = re.search(r"FILED AS OF DATE:\s+(\d+)", text)

    metadata["company_name"] = company_name_match.group(1).strip() if company_name_match else "Unknown"
    metadata["cik"] = cik_match.group(1).strip() if cik_match else "Unknown"
    metadata["filing_type"] = filing_type_match.group(1).strip() if filing_type_match else "Unknown"
    metadata["date"] = filed_date_match.group(1).strip() if filed_date_match else "Unknown"

    return metadata"""

<>:2: SyntaxWarning: invalid escape sequence '\s'
<>:2: SyntaxWarning: invalid escape sequence '\s'
C:\Users\sudet\AppData\Local\Temp\ipykernel_8108\3645909740.py:2: SyntaxWarning: invalid escape sequence '\s'
  """"""Extract metadata such as company name, CIK, filing type, and date.""""""


'def extract_metadata(text):\n    Extract metadata such as company name, CIK, filing type, and date.\n    metadata = {}\n    \n    company_name_match = re.search(r"COMPANY CONFORMED NAME:\\s+(.+)", text)\n    cik_match = re.search(r"CENTRAL INDEX KEY:\\s+(\\d+)", text)\n    filing_type_match = re.search(r"FORM TYPE:\\s+(\\S+)", text)\n    filed_date_match = re.search(r"FILED AS OF DATE:\\s+(\\d+)", text)\n\n    metadata["company_name"] = company_name_match.group(1).strip() if company_name_match else "Unknown"\n    metadata["cik"] = cik_match.group(1).strip() if cik_match else "Unknown"\n    metadata["filing_type"] = filing_type_match.group(1).strip() if filing_type_match else "Unknown"\n    metadata["date"] = filed_date_match.group(1).strip() if filed_date_match else "Unknown"\n\n    return metadata'

In [22]:
def extract_metadata(text):
    """Extract metadata such as company name, CIK, filing type, date, and additional fields from a 10-Q report."""
    metadata = {}
    
    # Extract company information
    company_name_match = re.search(r"COMPANY CONFORMED NAME:\s+(.+)", text)
    cik_match = re.search(r"CENTRAL INDEX KEY:\s+(\d+)", text)
    filing_type_match = re.search(r"FORM TYPE:\s+(\S+)", text)
    filed_date_match = re.search(r"FILED AS OF DATE:\s+(\d+)", text)
    period_of_report_match = re.search(r"PERIOD OF REPORT:\s+(\d+)", text)
    sec_file_match = re.search(r"SEC FILE NUMBER:\s+([\d-]+)", text)
    ein_match = re.search(r"IRS NUMBER:\s+(\d+)", text)
    sic_match = re.search(r"STANDARD INDUSTRIAL CLASSIFICATION:\s+(.+)", text)
    public_float_match = re.search(r"PUBLIC FLOAT:\s+\$([\d,]+)", text)
    outstanding_shares_match = re.search(r"OUTSTANDING SHARES:\s+([\d,]+)", text)

    # Store extracted metadata
    metadata["company_name"] = company_name_match.group(1).strip() if company_name_match else "Unknown"
    metadata["cik"] = cik_match.group(1).strip() if cik_match else "Unknown"
    metadata["filing_type"] = filing_type_match.group(1).strip() if filing_type_match else "Unknown"
    metadata["date"] = filed_date_match.group(1).strip() if filed_date_match else "Unknown"
    metadata["period_of_report"] = period_of_report_match.group(1).strip() if period_of_report_match else "Unknown"
    metadata["sec_file_number"] = sec_file_match.group(1).strip() if sec_file_match else "Unknown"
    metadata["ein"] = ein_match.group(1).strip() if ein_match else "Unknown"
    metadata["industry_classification"] = sic_match.group(1).strip() if sic_match else "Unknown"
    metadata["public_float"] = public_float_match.group(1).strip() if public_float_match else "Unknown"
    metadata["outstanding_shares"] = outstanding_shares_match.group(1).strip() if outstanding_shares_match else "Unknown"

    return metadata


In [23]:
def clean_filing_text(text):
    """Clean SEC filing text using BeautifulSoup to remove HTML/XBRL tags."""
    soup = BeautifulSoup(text, "lxml")  # Use lxml parser for efficiency
    clean_text = soup.get_text(separator=" ")  # Get readable text
    clean_text = re.sub(r"\s+", " ", clean_text).strip()  # Normalize spaces
    return clean_text

In [26]:
"""def process_filings(base_dir, csv_file="sec_filings.csv"):
    """"""Traverse SEC filings folder structure, extract relevant data, and update CSV.""""""
    
    # Load existing data if the CSV exists, otherwise create an empty DataFrame
    if os.path.exists(csv_file):
        existing_df = pd.read_csv(csv_file, dtype=str)  # Load as strings to prevent formatting issues
    else:
        existing_df = pd.DataFrame(columns=[
            "ticker", "company_name", "cik", "date", "filing_type", "period_of_report",
            "sec_file_number", "ein", "industry_classification", "public_float",
            "outstanding_shares", "filing_text"
        ])

    for ticker in os.listdir(base_dir):
        ticker_path = os.path.join(base_dir, ticker)
        if not os.path.isdir(ticker_path):  # Skip non-directory files
            continue

        for filing_type in ["10-Q"]:
            filing_path = os.path.join(ticker_path, filing_type)
            if not os.path.exists(filing_path):
                continue

            for filing_folder in os.listdir(filing_path):
                submission_path = os.path.join(filing_path, filing_folder, "full-submission.txt")
                if not os.path.exists(submission_path):
                    continue
                
                with open(submission_path, "r", encoding="utf-8", errors="ignore") as f:
                    content = f.read()
                
                metadata = extract_metadata(content)
                filing_text = clean_filing_text(content)

                # Create a unique key to check for duplicates (e.g., ticker + date + filing type)
                unique_key = f"{ticker}_{metadata['date']}_{metadata['filing_type']}"

                # Check if the unique entry already exists
                if not ((existing_df["ticker"] == ticker) &
                        (existing_df["date"] == metadata["date"]) &
                        (existing_df["filing_type"] == metadata["filing_type"])).any():
                    
                    new_data = []
                    
                    new_data.append({
                        "ticker": ticker,
                        "company_name": metadata["company_name"],
                        "cik": metadata["cik"],
                        "date": metadata["date"],
                        "filing_type": metadata["filing_type"],
                        "period_of_report": metadata["period_of_report"],
                        "sec_file_number": metadata["sec_file_number"],
                        "ein": metadata["ein"],
                        "industry_classification": metadata["industry_classification"],
                        "public_float": metadata["public_float"],
                        "outstanding_shares": metadata["outstanding_shares"],
                        "filing_text": filing_text
                    })
                    
                    print(f"Added new record for {metadata['company_name']} ({metadata['filing_type']} - {metadata['date']})")

                    # Append new data to existing DataFrame
                    if new_data:
                        new_df = pd.DataFrame(new_data)
                        updated_df = pd.concat([existing_df, new_df], ignore_index=True)

                        # Save the updated DataFrame to CSV
                        updated_df.to_csv(csv_file, index=False, encoding="utf-8")
                        print(f"CSV file updated successfully with {len(new_data)} new records.")

                    else:
                        print("No new records to add. CSV remains unchanged.")

"""

'def process_filings(base_dir, csv_file="sec_filings.csv"):\n    Traverse SEC filings folder structure, extract relevant data, and update CSV.\n    \n    # Load existing data if the CSV exists, otherwise create an empty DataFrame\n    if os.path.exists(csv_file):\n        existing_df = pd.read_csv(csv_file, dtype=str)  # Load as strings to prevent formatting issues\n    else:\n        existing_df = pd.DataFrame(columns=[\n            "ticker", "company_name", "cik", "date", "filing_type", "period_of_report",\n            "sec_file_number", "ein", "industry_classification", "public_float",\n            "outstanding_shares", "filing_text"\n        ])\n\n    for ticker in os.listdir(base_dir):\n        ticker_path = os.path.join(base_dir, ticker)\n        if not os.path.isdir(ticker_path):  # Skip non-directory files\n            continue\n\n        for filing_type in ["10-Q"]:\n            filing_path = os.path.join(ticker_path, filing_type)\n            if not os.path.exists(filing_path

In [ ]:
"""def process_filings(base_dir):
    """"""Traverse SEC filings folder structure and extract relevant data.""""""
    data = []

    for ticker in os.listdir(base_dir):
        ticker_path = os.path.join(base_dir, ticker)
        if not os.path.isdir(ticker_path):  # Skip non-directory files
            continue

        for filing_type in ["10-K", "10-Q"]:
            filing_path = os.path.join(ticker_path, filing_type)
            if not os.path.exists(filing_path):
                continue

            for filing_folder in os.listdir(filing_path):
                submission_path = os.path.join(filing_path, filing_folder, "full-submission.txt")
                if not os.path.exists(submission_path):
                    continue
                
                with open(submission_path, "r", encoding="utf-8", errors="ignore") as f:
                    content = f.read()
                
                metadata = extract_metadata(content)
                filing_text = clean_filing_text(content)

                data.append({
                    "ticker": ticker,
                    "company_name": metadata["company_name"],
                    "cik": metadata["cik"],
                    "date": metadata["date"],
                    "filing_type": metadata["filing_type"],
                    "filing_text": filing_text
                })
                
                print(f"Processed {metadata['company_name']} ({metadata['filing_type']})" ) 
    
    return pd.DataFrame(data)"""

In [5]:
DB_FILE = "sec_filings.db"

def create_database():
    """Initialize the SQLite database and create the filings table if it doesn't exist."""
    conn = sqlite3.connect(DB_FILE)
    cursor = conn.cursor()
    
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS filings (
            id INTEGER PRIMARY KEY AUTOINCREMENT,
            company_name TEXT,
            cik TEXT,
            filing_type TEXT,
            date TEXT,
            period_of_report TEXT,
            sec_file_number TEXT,
            ein TEXT,
            industry_classification TEXT,
            public_float TEXT,
            outstanding_shares TEXT,
            filing_text TEXT,
            UNIQUE(ticker, date, filing_type)  -- Prevents duplicates
        )
    """)
    
    conn.commit()
    conn.close()

def insert_filing(metadata, filing_text):
    """Insert new filing record into the database, avoiding duplicates."""
    conn = sqlite3.connect(DB_FILE)
    cursor = conn.cursor()

    try:
        cursor.execute("""
            INSERT INTO filings (company_name, cik, filing_type, date, period_of_report, 
                                sec_file_number, ein, industry_classification, public_float, 
                                outstanding_shares, filing_text)
            VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
        """, (
            metadata["company_name"], metadata["cik"], metadata["date"],
            metadata["filing_type"], metadata["period_of_report"], metadata["sec_file_number"],
            metadata["ein"], metadata["industry_classification"], metadata["public_float"],
            metadata["outstanding_shares"], filing_text
        ))

        conn.commit()
        print(f"Added: {metadata['company_name']} ({metadata['filing_type']} - {metadata['date']})")

    except sqlite3.IntegrityError:
        print(f"Skipping duplicate: {metadata['company_name']} ({metadata['filing_type']} - {metadata['date']})")

    conn.close()

def process_filings(base_dir):
    """Process SEC filings and store in a database."""
    create_database()  # Ensure database is set up

    for ticker in os.listdir(base_dir):
        ticker_path = os.path.join(base_dir, ticker)
        if not os.path.isdir(ticker_path):
            continue

        for filing_type in ["10-Q"]:
            filing_path = os.path.join(ticker_path, filing_type)
            if not os.path.exists(filing_path):
                continue

            for filing_folder in os.listdir(filing_path):
                submission_path = os.path.join(filing_path, filing_folder, "full-submission.txt")
                if not os.path.exists(submission_path):
                    continue
                
                with open(submission_path, "r", encoding="utf-8", errors="ignore") as f:
                    content = f.read()
                
                metadata = extract_metadata(content)
                filing_text = clean_filing_text(content)

                insert_filing(metadata, filing_text)  # Add to database

In [ ]:
# Run processing and save to CSV
process_filings(base_dir)

In [40]:
import os
import re
import pandas as pd
from bs4 import BeautifulSoup
import sqlite3  

# Base directory where SEC filings are stored
base_dir = "C:/Users/sudet/Desktop/sec-edgar-filings"  # Update this with the correct path
output_file = "sec_filings.csv"
DB_FILE = "sec_filings.db"

def extract_metadata(text, ticker):
    """Extract metadata such as company name, CIK, filing type, date, and additional fields from a 10-Q report."""
    metadata = {}
    
    # Extract company information
    company_name_match = re.search(r"COMPANY CONFORMED NAME:\s+(.+)", text)
    cik_match = re.search(r"CENTRAL INDEX KEY:\s+(\d+)", text)
    filing_type_match = re.search(r"FORM TYPE:\s+(\S+)", text)
    filed_date_match = re.search(r"FILED AS OF DATE:\s+(\d+)", text)
    period_of_report_match = re.search(r"PERIOD OF REPORT:\s+(\d+)", text)
    sec_file_match = re.search(r"SEC FILE NUMBER:\s+([\d-]+)", text)
    ein_match = re.search(r"IRS NUMBER:\s+(\d+)", text)
    sic_match = re.search(r"STANDARD INDUSTRIAL CLASSIFICATION:\s+(.+)", text)
    public_float_match = re.search(r"PUBLIC FLOAT:\s+\$([\d,]+)", text)
    outstanding_shares_match = re.search(r"OUTSTANDING SHARES:\s+([\d,]+)", text)
    
    # Store extracted metadata
    metadata["ticker"] = ticker  # Include the ticker from directory name
    metadata["company_name"] = company_name_match.group(1).strip() if company_name_match else "Unknown"
    metadata["cik"] = cik_match.group(1).strip() if cik_match else "Unknown"
    metadata["filing_type"] = filing_type_match.group(1).strip() if filing_type_match else "Unknown"
    metadata["date"] = filed_date_match.group(1).strip() if filed_date_match else "Unknown"
    metadata["period_of_report"] = period_of_report_match.group(1).strip() if period_of_report_match else "Unknown"
    metadata["sec_file_number"] = sec_file_match.group(1).strip() if sec_file_match else "Unknown"
    metadata["ein"] = ein_match.group(1).strip() if ein_match else "Unknown"
    metadata["industry_classification"] = sic_match.group(1).strip() if sic_match else "Unknown"
    metadata["public_float"] = public_float_match.group(1).strip() if public_float_match else "Unknown"
    metadata["outstanding_shares"] = outstanding_shares_match.group(1).strip() if outstanding_shares_match else "Unknown"

    return metadata

def clean_filing_text(text):
    """Clean SEC filing text using BeautifulSoup to remove HTML/XBRL tags."""
    soup = BeautifulSoup(text, "lxml")  
    clean_text = soup.get_text(separator=" ")  
    clean_text = re.sub(r"\s+", " ", clean_text).strip()  
    return clean_text

def create_database():
    """Initialize the SQLite database and create the filings table if it doesn't exist."""
    conn = sqlite3.connect(DB_FILE)
    cursor = conn.cursor()
    
    cursor.execute("""
        CREATE TABLE IF NOT EXISTS filings (
            id INTEGER PRIMARY KEY AUTOINCREMENT,
            ticker TEXT,
            company_name TEXT,
            cik TEXT,
            filing_type TEXT,
            date TEXT,
            period_of_report TEXT,
            sec_file_number TEXT,
            ein TEXT,
            industry_classification TEXT,
            public_float TEXT,
            outstanding_shares TEXT,
            filing_text TEXT,
            UNIQUE(ticker, date, filing_type)  -- Prevents duplicates
        )
    """)
    
    conn.commit()
    conn.close()

def insert_filing(metadata, filing_text):
    """Insert new filing record into the database, avoiding duplicates."""
    conn = sqlite3.connect(DB_FILE)
    cursor = conn.cursor()
    
    try:
        cursor.execute("""
            INSERT INTO filings (ticker, company_name, cik, filing_type, date, period_of_report, 
                                sec_file_number, ein, industry_classification, public_float, 
                                outstanding_shares, filing_text)
            VALUES (?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?, ?)
        """, (
            metadata["ticker"], metadata["company_name"], metadata["cik"], metadata["filing_type"], 
            metadata["date"], metadata["period_of_report"], metadata["sec_file_number"], 
            metadata["ein"], metadata["industry_classification"], metadata["public_float"], 
            metadata["outstanding_shares"], filing_text
        ))

        conn.commit()
        print(f"Added: {metadata['company_name']} ({metadata['filing_type']} - {metadata['date']})")
    
    except sqlite3.IntegrityError:
        print(f"Skipping duplicate: {metadata['company_name']} ({metadata['filing_type']} - {metadata['date']})")
    
    conn.close()

def process_filings(base_dir):
    """Process SEC filings and store in a database."""
    create_database()  
    
    for ticker in os.listdir(base_dir):
        ticker_path = os.path.join(base_dir, ticker)
        if not os.path.isdir(ticker_path):
            continue
        
        for filing_type in ["10-Q"]:
            filing_path = os.path.join(ticker_path, filing_type)
            if not os.path.exists(filing_path):
                continue
            
            for filing_folder in os.listdir(filing_path):
                submission_path = os.path.join(filing_path, filing_folder, "full-submission.txt")
                if not os.path.exists(submission_path):
                    continue
                
                with open(submission_path, "r", encoding="utf-8", errors="ignore") as f:
                    content = f.read()
                
                metadata = extract_metadata(content, ticker)
                filing_text = clean_filing_text(content)
                insert_filing(metadata, filing_text)  

# Run processing
process_filings(base_dir)

Skipping duplicate: AMERICAN ELECTRIC POWER COMPANY INC (10-Q - 20000515)
Skipping duplicate: AMERICAN ELECTRIC POWER COMPANY INC (10-Q - 20000814)
Skipping duplicate: AMERICAN ELECTRIC POWER COMPANY INC (10-Q - 20001114)
Skipping duplicate: AMERICAN ELECTRIC POWER COMPANY INC (10-Q - 20010515)
Skipping duplicate: AMERICAN ELECTRIC POWER COMPANY INC (10-Q - 20010815)
Skipping duplicate: AMERICAN ELECTRIC POWER COMPANY INC (10-Q - 20011114)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20020515)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20020813)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20021114)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20030514)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20030812)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20031112)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20040507)
Skipping duplicate: AMERICAN ELECTRIC POWER CO INC (10-Q - 20040806)
Skip

KeyboardInterrupt: 

In [41]:
import sqlite3

# Connect to the database
conn = sqlite3.connect(DB_FILE)
cursor = conn.cursor()

# Query to get the number of rows and columns
cursor.execute("SELECT COUNT(*) FROM filings")
num_rows = cursor.fetchone()[0]

cursor.execute("PRAGMA table_info(filings)")
num_columns = len(cursor.fetchall())

company_tickers = cursor.execute("SELECT DISTINCT ticker FROM filings").fetchall()

# Close the connection
conn.close()

# Print the shape
print(f"Shape of the filings table: ({num_rows}, {num_columns})")
print(f"Companies in this dataset: {company_tickers}")

Shape of the filings table: (4600, 13)
Companies in this dataset: [('A',), ('AAPL',), ('ABBV',), ('ABNB',), ('ABT',), ('ACGL',), ('ACN',), ('ADBE',), ('ADI',), ('ADP',), ('ADSK',), ('AEE',), ('AEP',), ('AFL',), ('AIG',), ('AJG',), ('ALL',), ('ALNY',), ('AMAT',), ('AMD',), ('AME',), ('AMGN',), ('AMP',), ('AMT',), ('AMZN',), ('ANET',), ('ANSS',), ('AON',), ('APD',), ('APH',), ('APO',), ('APP',), ('ARES',), ('AVB',), ('AVGO',), ('AWK',), ('AXON',), ('AXP',), ('AZO',), ('BA',), ('BAC',), ('BDX',), ('BK',), ('BKNG',), ('BKR',), ('BLK',), ('BMY',), ('BR',), ('BRK-B',), ('BRO',), ('BSX',), ('BX',), ('C',), ('CAH',), ('CARR',), ('CAT',), ('CB',), ('CBRE',), ('CCI',), ('CCL',), ('CDNS',), ('CEG',), ('CHD',), ('CHTR',), ('CI',), ('CL',), ('CMCSA',), ('CME',), ('CMG',), ('CMI',), ('CNC',), ('COF',), ('COIN',), ('COP',), ('COR',), ('COST',), ('CP',), ('CPNG',), ('CPRT',), ('CQP',), ('CRH',), ('CRM',), ('CRWD',), ('CSCO',), ('CSGP',), ('CSX',), ('CTAS',)]


In [47]:
# Connect to the database
conn = sqlite3.connect(DB_FILE)
cursor = conn.cursor()

# Query to get the filing text of the first element
cursor.execute("SELECT filing_text FROM filings LIMIT 10")
first_filing_text = cursor.fetchone()[0]

# Close the connection
conn.close()

# Print the filing text
first_filing_text

'-----BEGIN PRIVACY-ENHANCED MESSAGE----- Proc-Type: 2001,MIC-CLEAR Originator-Name: webmaster@www.sec.gov Originator-Key-Asymmetric: MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB MIC-Info: RSA-MD5,RSA, WmkAS8ih2FrKCipqV3W9ucPOb9wthnfSJV24oE6p8n+AFVrwCeFaBtZL/TCNpuYE 8KWTqEEaTixVDrfXOmm5jQ== 0000891618-01-501182.txt : 20010615 0000891618-01-501182.hdr.sgml : 20010615 ACCESSION NUMBER: 0000891618-01-501182 CONFORMED SUBMISSION TYPE: 10-Q PUBLIC DOCUMENT COUNT: 2 CONFORMED PERIOD OF REPORT: 20010430 FILED AS OF DATE: 20010614 FILER: COMPANY DATA: COMPANY CONFORMED NAME: AGILENT TECHNOLOGIES INC CENTRAL INDEX KEY: 0001090872 STANDARD INDUSTRIAL CLASSIFICATION: INSTRUMENTS FOR MEAS & TESTING OF ELECTRICITY & ELEC SIGNALS [3825] IRS NUMBER: 770518772 STATE OF INCORPORATION: DE FISCAL YEAR END: 1031 FILING VALUES: FORM TYPE: 10-Q SEC ACT: SEC FILE NUMBER: 001-15405 FILM NUMBER: 1660354 BUSINESS ADDRESS: STREET 1: 395

In [48]:
# Connect to the database
conn = sqlite3.connect(DB_FILE)
cursor = conn.cursor()

# Query to get the first row
cursor.execute("SELECT * FROM filings LIMIT 1")
first_row = cursor.fetchone()

# Close the connection
conn.close()

# Print the first row
print(first_row)

(1, 'A', 'AGILENT TECHNOLOGIES INC', '0001090872', '20010614', '10-Q', '20010430', '001-15405', '770518772', 'INSTRUMENTS FOR MEAS & TESTING OF ELECTRICITY & ELEC SIGNALS [3825]', 'Unknown', 'Unknown', '-----BEGIN PRIVACY-ENHANCED MESSAGE----- Proc-Type: 2001,MIC-CLEAR Originator-Name: webmaster@www.sec.gov Originator-Key-Asymmetric: MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB MIC-Info: RSA-MD5,RSA, WmkAS8ih2FrKCipqV3W9ucPOb9wthnfSJV24oE6p8n+AFVrwCeFaBtZL/TCNpuYE 8KWTqEEaTixVDrfXOmm5jQ== 0000891618-01-501182.txt : 20010615 0000891618-01-501182.hdr.sgml : 20010615 ACCESSION NUMBER: 0000891618-01-501182 CONFORMED SUBMISSION TYPE: 10-Q PUBLIC DOCUMENT COUNT: 2 CONFORMED PERIOD OF REPORT: 20010430 FILED AS OF DATE: 20010614 FILER: COMPANY DATA: COMPANY CONFORMED NAME: AGILENT TECHNOLOGIES INC CENTRAL INDEX KEY: 0001090872 STANDARD INDUSTRIAL CLASSIFICATION: INSTRUMENTS FOR MEAS & TESTING OF ELECTRICITY & ELEC SIG

In [7]:
# Connect to the database
conn = sqlite3.connect(DB_FILE)
cursor = conn.cursor()

# Query to get the filing texts of the first 5 companies
cursor.execute("""
    SELECT DISTINCT ticker, filing_text 
    FROM filings 
    GROUP BY ticker 
    LIMIT 5
""")
first_5_filings = cursor.fetchall()

# Close the connection
conn.close()

# Print the filing texts
for ticker, filing_text in first_5_filings:
    print(f"Ticker: {ticker}\nFiling Text: {filing_text}\n")

Ticker: A
Filing Text: -----BEGIN PRIVACY-ENHANCED MESSAGE----- Proc-Type: 2001,MIC-CLEAR Originator-Name: webmaster@www.sec.gov Originator-Key-Asymmetric: MFgwCgYEVQgBAQICAf8DSgAwRwJAW2sNKK9AVtBzYZmr6aGjlWyK3XmZv3dTINen TWSM7vrzLADbmYQaionwg5sDW3P6oaM5D3tdezXMm7z1T+B+twIDAQAB MIC-Info: RSA-MD5,RSA, AxzCmlHFgyFtJE5UTZ0EPPaoDeJ1Bb2+X0gw7WHuqX/436Plp/zPjiLjVrafTLjL cPs7M96SWYrAB7uZGZ/dEw== 0000912057-00-011701.txt : 20000316 0000912057-00-011701.hdr.sgml : 20000316 ACCESSION NUMBER: 0000912057-00-011701 CONFORMED SUBMISSION TYPE: 10-Q PUBLIC DOCUMENT COUNT: 2 CONFORMED PERIOD OF REPORT: 20000131 FILED AS OF DATE: 20000315 FILER: COMPANY DATA: COMPANY CONFORMED NAME: AGILENT TECHNOLOGIES INC CENTRAL INDEX KEY: 0001090872 STANDARD INDUSTRIAL CLASSIFICATION: INSTRUMENTS FOR MEAS & TESTING OF ELECTRICITY & ELEC SIGNALS [3825] IRS NUMBER: 770518772 STATE OF INCORPORATION: DE FISCAL YEAR END: 1031 FILING VALUES: FORM TYPE: 10-Q SEC ACT: SEC FILE NUMBER: 001-15405 FILM NUMBER: 570392 BUSINESS A